# Problema


Dado uma lista de produtos com descrição e sugestões de como realizar a venda desses produtos construa textos persuasivos para ações de Marketing e Vendas.

# 1.   Configurações

Importações e definição de variáveis de escopo global

In [ ]:
!pip install langchain==0.0.348
!pip install openai==1.3.8
!pip install pydantic==1.10.8
!pip install chromadb==0.4.18
!pip install tiktoken==0.5.2
!pip install sentence-transformers==2.3.0
!pip install deeplake==3.8.17
!pip install tiktoken==0.5.2
!pip install gradio==3.45.0

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.0/2.0 MB 13.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 188.2/188.2 kB 20.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 54.4/54.4 kB 7.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.4/49.4 kB 5.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 221.5/221.5 kB 5.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 75.9/75.9 kB 8.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 76.9/76.9 kB 8.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 7.7 MB/s eta 0:00:00
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
llmx 0.0.15a0 requires cohere, which is not installed.
llmx 0.0.15a0 requires tiktoken, which is not installed.
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.1/3.1 MB 13.3 MB/s et

In [ ]:
!python -m spacy download pt_core_news_sm

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.0/13.0 MB 21.6 MB/s eta 0:00:00
✔ Download and installation successful
You can now load the package via spacy.load('pt_core_news_sm')


In [ ]:
import pandas as pd
import unicodedata
import requests
import json
import os
import tiktoken
from openai import OpenAI
from langchain.document_loaders import DataFrameLoader
from langchain.embeddings import HuggingFaceEmbeddings
from langchain.text_splitter import CharacterTextSplitter
from langchain.vectorstores import DeepLake
from langchain.prompts import ChatPromptTemplate
from langchain.chat_models import ChatOpenAI
from langchain.schema.output_parser import StrOutputParser
from google.colab import userdata
from langchain.schema.runnable import RunnableParallel
from langchain.chains.summarize import load_summarize_chain
from langchain.prompts import PromptTemplate

TOKEN_ML = userdata.get('TOKEN_ML')
OPENAI_API_KEY = userdata.get('OPENAI_KEY')

os.environ['OPENAI_API_KEY'] = userdata.get('OPENAI_API_KEY')

client = OpenAI()
OpenAI.api_key = OPENAI_API_KEY

/usr/local/lib/python3.10/dist-packages/deeplake/util/check_latest_version.py:32: UserWarning: A newer version of deeplake (3.8.18) is available. It's recommended that you update to the latest version using `pip install -U deeplake`.
  warnings.warn(


# 2.   Coleta de dados

*Descrição de produtos da Amazon (2020)*

In [ ]:
# df_amazon = pd.read_csv('marketing_sample_for_amazon_com-ecommerce__20200101_20200131__10k_data.csv')

In [ ]:
# print(df_amazon[['Uniq Id', 'Product Name', 'About Product']].tail(10).to_string())

*Extrator de descrição de produtos do Mercado Livre*

In [ ]:
!gdown 1dY0n-LdyH2t5xC7wY2SgLQVT7wGie6oE

Downloading...
From: https://drive.google.com/uc?id=1dY0n-LdyH2t5xC7wY2SgLQVT7wGie6oE
To: /content/mercado_livre_products_full_drive.csv
100% 54.3M/54.3M [00:01<00:00, 35.4MB/s]


In [ ]:
def get_ml_product_descriptions():
    f = open('/content/ml_categories.json', 'r')

    categories_json = json.load(f)

    categories_to_save = {}

    # df = pd.DataFrame(columns=['id', 'category', 'sub_category', 'title', 'description'])
    df = pd.read_csv('/content/mercado_livre_products_full_drive.csv')

    for item in categories_json:
        category = {'name': categories_json[item]['name'], 'id': categories_json[item]['id']}

        for sub_category in categories_json[item]['children_categories']:
            offset = 0
            limit = 50
            while offset < 1000:

                headers = {'Authorization': f'Bearer {TOKEN_ML}'}
                ans = \
                    requests.get(f"https://api.mercadolibre.com/sites/MLB/search?category="
                                 f"{sub_category['id']}&search_type=scan&offset={offset}&limit=50",
                                 headers=headers)

                if ans.ok:
                    data_ans = ans.json()

                    print(f"[{sub_category['name']}]: {100.0*(offset/int(data_ans['paging']['total']))} downloaded...")

                    if len(data_ans['results']) == 0:
                        break

                    lt_prod_info = [{'id': info['id'], 'title': info['title']} for info in data_ans['results']]

                    for info in lt_prod_info:
                        resp = requests.get(f"https://api.mercadolibre.com/items/{info['id']}/description", headers=headers)

                        if resp.ok:
                            data_resp = resp.json()
                            if 'plain_text' in data_resp:
                                info['description'] = data_resp['plain_text']

                    df_tmp = pd.DataFrame.from_dict(lt_prod_info)
                    df_tmp['category'] = category['name']
                    df_tmp['sub_category'] = sub_category['name']

                    df: pd.DataFrame = pd.concat([df, df_tmp])

                    df.to_csv('/content/mercado_livre_products_full_drive.csv', header=True, index=False)
                else:
                    print(f'FAIL! Error {ans.status_code}: {ans.content}')

                offset = offset + limit + 1

In [ ]:
def enrich_with_google_search():
  df = pd.read_csv('/content/mercado_livre_products_full_drive.csv')

  df = df[df['category'] == 'Acessórios para Veículos']

  df.to_csv('/content/mercado_livre_products_full_drive.csv', header=True, index=False)

  p_names = list(set(df['title'].to_list()))
  map_name = {}
  k = 0

  for name in p_names:
      url = 'https://www.google.com/search?q=' + quote('[o que é,descrição,sobre -procurando por]: ' + name)

      req = Request(url, headers={'User-Agent': 'Mozilla/5.0'})

      lt_text = []

      try:
          response = urllib.request.urlopen(req)

          if response.code == 429:
              print(f'Sleeping {int(response.headers["Retry-After"])} seconds...')
              time.sleep(int(response.headers["Retry-After"]))

          content = response.read().decode('UTF-8').replace(u'\xa0', u' ')

          soup = BeautifulSoup(content, 'html.parser')

          div_bs4 = soup.find_all('div', {"class":"BNeawe s3v9rd AP7Wnd"})

          lt_text = [p.get_text() for p in div_bs4]
      except Exception as error:
          print(error)

      map_name[name] = ', '.join(lt_text)

      df2 = pd.read_csv('/content/mercado_livre_products_full_drive.csv')

      df2['about'] = df2['title'].map(map_name)

      df2.to_csv('/content/mercado_livre_products_full_drive.csv', header=True, index=False)

      k = k + 1
      print(f'[{k} of {len(p_names)}]: {(k / len(p_names)) * 100.0}% completed')

      time.sleep(1)

In [ ]:
df_ml = pd.read_csv('/content/mercado_livre_products_full_drive.csv', low_memory=False)
print(df_ml.shape[0])
print(df_ml.tail(10).to_string())

21648
                  id                  category sub_category                                                                             title                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                     

# 3. Limpeza e pré-processamento dos dados

Realizar a limpeza do texto removendo informações irrelevantes


In [ ]:
df_ml = df_ml[~(df_ml['description'].isna() | df_ml['about'].isna())]
print(df_ml.tail(10).to_string())

                  id                  category sub_category                                                         title                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                               

In [ ]:
import spacy
from spacy.lang.pt import Portuguese

nlp = spacy.load("pt_core_news_sm")

def count_tokens(text):
  encoding = tiktoken.encoding_for_model("gpt-3.5-turbo")
  return len(encoding.encode(text))

def text_to_chunks(text):
  chunks = [[]]
  chunk_total_words = 0

  sentences = nlp(text)

  for sentence in sentences.sents:
    chunk_total_words += len(sentence.text.split(" "))

    if chunk_total_words > 2000:
      chunks.append([])
      chunk_total_words = len(sentence.text.split(" "))

    chunks[len(chunks)-1].append(sentence.text)

  return chunks

def chat_gpt_summarize(text):
  prompt = f"Resuma o seguinte texto em no máximo 5 frases:\n{text}"

  response = client.completions.create(
    model="gpt-3.5-turbo-instruct",
    prompt=prompt,
    temperature=0.3,
    max_tokens=150,
    top_p=1,
    frequency_penalty=0,
    presence_penalty=1
  )

  return response.choices[0].text

def summarize_text(text):

  chunks = text_to_chunks(text)

  chunk_summaries = []

  for chunk in chunks:
    chunk_summary = chat_gpt_summarize(" ".join(chunk))
    chunk_summaries.append(chunk_summary)
    break

  summary = " ".join(chunk_summaries)

  return summary

def find_best_position_to_cut(text):
  lo = 0
  hi = len(text)-1
  mid = hi

  while(lo <= hi):
    mid = (lo + hi) >> 1

    if count_tokens(text[0:mid]) >= 1000:
      hi = mid - 1
    else:
      lo = mid + 1

  return mid


In [ ]:
df_ml = df_ml[df_ml['category'] == 'Acessórios para Veículos']

df_ml['description'] = df_ml['description'].apply(lambda x: x[0: find_best_position_to_cut(x)+1])
df_ml['about'] = df_ml['about'].apply(lambda x: x[0: find_best_position_to_cut(x)+1])

df_ml['size'] = df_ml['description'].apply(lambda x: count_tokens(x))

df_ml = df_ml.sort_values(by=['size'], ascending=False)

df_ml['sequence'] = df_ml.groupby('sub_category').cumcount()

df_ml = df_ml[(df_ml['sequence'] <= 5)]

df_ml = df_ml.reset_index(drop=True)

print(df_ml.tail(10).to_string())

                id                  category                  sub_category                                                         title                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                

In [ ]:
df_ml = df_ml[df_ml['category'] == 'Acessórios para Veículos']

df_ml['sales_pitch'] = df_ml[['sub_category', 'title', 'description']].apply(lambda x: f'Nome do produto:{x[0]}\nCategoria do produto:{x[1]}\nSugestão de como vender:{x[2]}', axis=1)
df_ml['about'] = df_ml[['sub_category', 'title', 'about']].apply(lambda x: f'Nome do produto:{x[0]}\nCategoria do produto:{x[1]}\nSobre o produto:{x[2]}', axis=1)

# df_ml['sales_pitch'] = df_ml['sales_pitch'].apply(lambda x: chat_gpt_summarize(x))
# map_about = {}
# lt_about = list(df_ml[['id', 'about']].apply(lambda x: {'id': x[0], 'about': x[1]}, axis=1).to_list())

# for about in lt_about:
#   map_about[about['id']] = chat_gpt_summarize(about['about'])

# df_ml['about'] = df_ml['about'].map(map_about)

df_ml = df_ml[['title', 'category', 'sub_category', 'sales_pitch', 'about']]

# df_ml = df_ml.head(50)

print(df_ml.shape[0])
print(df_ml.tail(10).to_string())

138
                                                            title                  category                  sub_category                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                           

# 4. Embedding

In [ ]:
loader_sales_pitch = DataFrameLoader(df_ml, page_content_column="sales_pitch")
documents_sales_pitch = loader_sales_pitch.load()
documents_sales_pitch.extend(loader_sales_pitch.load_and_split())

In [ ]:
loader_about = DataFrameLoader(df_ml, page_content_column="about")
documents_about = loader_about.load()
documents_about.extend(loader_about.load_and_split())

In [ ]:
!gdown 11CA58XtVtqiLTpxDY3YLvfkPV37ROsSc

!unzip -q my_deeplake.zip

Downloading...
From: https://drive.google.com/uc?id=11CA58XtVtqiLTpxDY3YLvfkPV37ROsSc
To: /content/my_deeplake.zip
100% 3.98M/3.98M [00:00<00:00, 22.9MB/s]


In [ ]:

text_splitter = CharacterTextSplitter(chunk_size=2000, separator='\n', chunk_overlap=0)

docs_sales_pitch = text_splitter.split_documents(documents_sales_pitch)
docs_about = text_splitter.split_documents(documents_sales_pitch)

embeddings = HuggingFaceEmbeddings()

vectorstore_sales_pitch = DeepLake(dataset_path="/content/my_deeplake/sales_pitch/", embedding_function=embeddings)
# vectorstore_sales_pitch.add_documents(docs_sales_pitch)

vectorstore_about = DeepLake(dataset_path="/content/my_deeplake/about/", embedding_function=embeddings)
# vectorstore_about.add_documents(docs_about)


Deep Lake Dataset in /content/my_deeplake/sales_pitch/ already exists, loading from the storage


Deep Lake Dataset in /content/my_deeplake/about/ already exists, loading from the storage


In [ ]:
# %cd /content/sample_data/

# !zip -r /content/my_deeplake.zip my_deeplake

# %cd /content/

In [ ]:
retriever_sales_pitch = vectorstore_sales_pitch.as_retriever()
retriever_about = vectorstore_about.as_retriever()


output_parser = StrOutputParser()
model = ChatOpenAI(openai_api_key=OPENAI_API_KEY, model="gpt-3.5-turbo")

# 5. Geração de texto (Copywriting)



In [ ]:
template = """Com base nas seguintes informações de produtos fornecidas abaixo:

{about}

Crie um discurso muito convincente e interessante de venda para os seguintes produtos:

{products}

Que fazem parte da sub_categoria:

{sub_category}

Pontue bem as vantagens dos produtos e suas caracteristicas bem como a grande oportunidade que o cliente está tendo em adquiri-los

Tenha como base os seguintes discursos de venda:

{sales_pitch}

Não fique preso apenas um discurso de venda. Leve mais em consideração a construção dos discrusos bem como as vantagens, caracterisitcas e descrição dos produtos.

Adicione preços para os produtos como variáveis com prefixo _PRECO_

"""

prompt = ChatPromptTemplate.from_template(template)

chain = RunnableParallel({
    "sales_pitch": lambda x: retriever_sales_pitch.get_relevant_documents(x["products"])[0:1],
    "about": lambda x:  retriever_about.get_relevant_documents(x["products"])[0:1],
    "products": lambda x: x["products"],
    "sub_category": lambda x: x["sub_category"]
}) | prompt | model | output_parser

In [ ]:
copywriting = chain.invoke({"products": "capacete", "sub_category": "Moto"})

In [ ]:
print(copywriting)

Olá, caro cliente! Temos uma grande oportunidade para você adquirir os melhores capacetes de moto da categoria! Nossos capacetes são fabricados com materiais de primeira qualidade, garantindo a sua segurança e conforto durante suas viagens de moto.

Um dos nossos destaques é o Capacete Moto X, que está disponível por apenas R$ _PRECO_CAPACETE_MOTO_X_. Esse capacete é feito com materiais de alta resistência, proporcionando uma excelente proteção para a sua cabeça. Além disso, ele possui um design moderno e aerodinâmico, que o torna muito mais confortável e estiloso.

Outra opção incrível é o Capacete Moto Y, que está com um preço especial de R$ _PRECO_CAPACETE_MOTO_Y_. Esse capacete é perfeito para quem busca segurança e estilo. Ele conta com um sistema de ventilação eficiente, que garante um fluxo de ar constante e evita o acúmulo de calor dentro do capacete. Além disso, ele possui uma viseira resistente a riscos, que proporciona uma visão clara e nítida durante suas viagens.

E não po

In [ ]:
print(copywriting)


Caro cliente, tenho uma grande oportunidade para você adquirir uma moto incrível! Apresento a você a nossa moto de última geração, com características e vantagens exclusivas.

Esta moto possui um motor potente e eficiente, que proporciona uma experiência de pilotagem incrível. Com uma velocidade máxima impressionante, você poderá desfrutar de viagens emocionantes e chegar aos seus destinos de forma rápida e segura.

Além disso, a moto conta com tecnologia avançada, incluindo um sistema de freios ABS que garante uma frenagem precisa e segura em qualquer situação. Isso significa que você terá um maior controle sobre a moto, mesmo em condições adversas.

Outra vantagem desta moto é o seu design moderno e aerodinâmico, que não apenas proporciona um visual elegante, mas também melhora a estabilidade e a performance. Com linhas arrojadas e acabamentos de alta qualidade, esta moto certamente chamará a atenção por onde passar.

E o melhor de tudo, estamos oferecendo um preço especial para esta

In [ ]:
print(copywriting)

Prezado cliente,

Gostaria de apresentar a você uma oportunidade imperdível para adquirir o kit de 2 pneus 195/55R16 Continental PowerContact 2 87H. Este pneu é especialmente desenvolvido para veículos médios e compactos, oferecendo uma série de vantagens que certamente vão te surpreender.

Uma das principais características do PowerContact 2 é a sua capacidade de proporcionar uma maior economia de combustível. Com a tecnologia avançada da Continental, esse pneu reduz o atrito com o solo, o que resulta em menor consumo de combustível e maior eficiência para o seu veículo. Com os preços competitivos que oferecemos, você pode economizar ainda mais na manutenção do seu carro.

Além disso, o PowerContact 2 se destaca pelo excelente conforto sonoro que proporciona. Com um desenho de banda de rodagem otimizado, esse pneu reduz significativamente o ruído durante a condução, garantindo uma viagem tranquila e silenciosa.

Outra vantagem do PowerContact 2 é a sua excelente dirigibilidade e robus

In [ ]:
print(copywriting)

Olá, cliente!

Gostaria de apresentar para você uma grande oportunidade de adquirir pneus de alta qualidade por preços acessíveis. Aqui na nossa loja, estamos com uma forte presença no mercado livre e atendemos clientes em todo o Brasil. Temos uma variedade de produtos em nosso catálogo, incluindo pneus, para atender todas as suas necessidades.

Nossos pneus são fabricados com materiais de alta durabilidade e resistência, garantindo assim uma ótima performance e segurança para o seu veículo. Além disso, oferecemos pneus para diferentes aros, desde R13 até R20, para atender todos os tipos de carros, desde os de passeio até utilitários, caminhonetes e SUVs.

Sabemos que imprevistos acontecem e todos já precisaram encostar o carro por conta de um pneu furado. Por isso, é importante contar com pneus de qualidade para evitar esse tipo de problema. Com os nossos pneus, você terá a tranquilidade de saber que está adquirindo um produto confiável e resistente.

Além disso, estamos oferecendo um

In [ ]:
print(copywriting)

Caro cliente, gostaria de lhe apresentar uma oportunidade incrível para adquirir um farol de alta qualidade e desempenho a um preço irresistível. Com o Farol original da marca XYZ, você terá a garantia de um produto durável, resistente e com excelente iluminação.

Nossos faróis são desenvolvidos com tecnologia avançada, proporcionando uma iluminação mais clara e nítida, garantindo maior segurança e visibilidade durante a noite ou em condições de baixa luminosidade.

Além disso, o farol XYZ possui uma instalação fácil e rápida, permitindo que você mesmo possa fazer a substituição sem a necessidade de um profissional. Isso significa economia de tempo e dinheiro.

E o melhor de tudo, estamos oferecendo um preço especial para você. Aproveite a oportunidade e adquira o Farol XYZ por apenas R$ _PRECO_FAROL_. Isso mesmo, um produto de alta qualidade com um preço que cabe no seu bolso.

Não perca mais tempo, garanta agora mesmo o seu Farol XYZ e tenha a certeza de estar adquirindo um produto c

In [ ]:
print(copywriting)

🌟🌟🌟 Atenção, amantes de motos! 🌟🌟🌟

🏍️ Você está procurando um farol incrível para sua Yamaha Factor 125, de 2009 a 2016? Então você está no lugar certo! Apresento a vocês o Farol Yamaha Factor 125 Completo, o acessório perfeito para deixar sua moto ainda mais estilosa e garantir uma pilotagem segura.

💡 Quais são as vantagens deste farol, você deve estar se perguntando? Deixe-me contar! Este farol é completo e montado, seguindo o modelo original da sua moto. Isso significa que você terá uma peça de alta qualidade, compatível com os modelos de motos Yamaha Factor 125 de 2009 a 2016. Além disso, ele é fabricado por uma marca renomada, garantindo durabilidade e resistência.

✨ Mas as vantagens não param por aí! Este farol é super fácil de instalar, você mesmo pode fazer isso em casa. E para te deixar ainda mais animado, temos uma oferta imperdível para você hoje! O Farol Yamaha Factor 125 Completo está disponível por apenas R$ _PRECO_FAROL_. Isso mesmo, um preço super especial para você,